In [1]:
import numpy as np
import pandas as pd


In [2]:
cluster_fp = "Data\\fine_clusters_birch_thresh_60_with_colornames.csv"
df_clusters = pd.read_csv(cluster_fp, delimiter=";")
df_clusters.head()

Unnamed: 0.1  Unnamed: 0                   id platform        hashtag  \
0             0           0  7172368921318657322   tiktok  climatechange   
1             1           0  7172368921318657322   tiktok  climatechange   
2             2           0  7172368921318657322   tiktok  climatechange   
3             3           0  7172368921318657322   tiktok  climatechange   
4             4           0  7172368921318657322   tiktok  climatechange   

          r         g         b         h         s         v  \
0  0.892157  0.816215  0.676990  0.107843  0.241176  0.892157   
1  0.678431  0.416637  0.242107  0.066667  0.643137  0.678431   
2  0.531373  0.531373  0.531373  0.000000  0.000000  0.531373   
3  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
4  0.482353  0.272388  0.321791  0.960784  0.435294  0.482353   

   relative_frequency      colorname  
0            0.004774         yellow  
1            0.086914  orange-yellow  
2            0.031250           gray  
3            0.099501          black  
4            0.072374     red-orange

In [3]:
columns = ["id", "platform", "hashtag", "n_clusters",
                                  "mean_r", "mean_g", "mean_b", "mean_h", "mean_s", "mean_v",
                                  "dominant_r", "dominant_g", "dominant_b", "dominant_h", "dominant_s", "dominant_v",
                                  "black", "gray", "white", "orange", "orange-yellow", "yellow", "yellow-green", "green", "green-blue", "blue", "blue-violet", "violet", "violet-red", "red", "red-orange"]
df_images = pd.DataFrame(columns=columns)
total_n_images = len(df_clusters["id"].unique())
n_images = 0
print(len(df_clusters["id"].unique()))
for image_id in df_clusters["id"].unique():
    image_specific_clusters = df_clusters[df_clusters["id"] == image_id]
    n_clusters = len(image_specific_clusters)
    platform = image_specific_clusters.platform.mode()[0]
    hashtag = image_specific_clusters.hashtag.mode()[0]
    init_values = [[image_id, 
                    platform,
                    hashtag,
                    n_clusters,
                    0.0, 0.0, 0.0, 0.0, 0.0, 0.0,
                    0.0, 0.0, 0.0, 0.0, 0.0, 0.0,
                    0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]]
    new_row = pd.DataFrame(init_values,columns=columns)
    
    new_row.at[0,"id"] = image_id
    #new_row.at[0,"platform"] = platform
    #new_row.at[0,"hashtag"] = hashtag
    new_row.at[0,"n_clusters"] = n_clusters

    max_frac = -1.0
    for idx, row in image_specific_clusters.iterrows():
        frac = row["relative_frequency"]
        if frac > max_frac:
            max_frac = frac
            new_row.at[0,"dominant_h"] = row["h"]
            new_row.at[0,"dominant_s"] = row["s"]
            new_row.at[0,"dominant_v"] = row["v"]
            new_row.at[0,"dominant_r"] = row["r"]
            new_row.at[0,"dominant_g"] = row["g"]
            new_row.at[0,"dominant_b"] = row["b"]

        new_row.at[0,"mean_h"] += frac * row["h"]
        new_row.at[0,"mean_s"] += frac * row["s"]
        new_row.at[0,"mean_v"] += frac * row["v"]
        new_row.at[0,"mean_r"] += frac * row["r"]
        new_row.at[0,"mean_g"] += frac * row["g"]
        new_row.at[0,"mean_b"] += frac * row["b"]

        new_row.at[0,row["colorname"]] += frac
    
    print (f"\r {n_images}/{total_n_images}", end="")
    n_images += 1
    #print(image_id)
    #print(new_row)
    
    df_images = pd.concat([df_images, new_row], axis=0)
    #print(df_images["platform"])
df_images.reset_index(inplace=True)
print("\n",len(df_images))
df_images.head()

6623
 3385/6623

In [15]:
df_images["max_colorname"] = ""
for idx, row in df_images.iterrows():
    print("ROW")
    print(row)
    max_frac = 0.0
    max_color = ""
    for color in ["black", "gray", "white", "orange", "orange-yellow", "yellow", "yellow-green", "green", "green-blue", "blue", "blue-violet", "violet", "violet-red", "red", "red-orange"]:
        frac = row[color]
        if frac > max_frac:
            max_frac = frac
            max_color = color
    df_images.at[idx, "max_colorname"] = max_color
    print(idx)

df_images.sample(50)

ROW
index                              0
id               7172368921318657322
platform                      tiktok
hashtag                climatechange
n_clusters                        12
mean_r                       0.22998
mean_g                      0.304649
mean_b                      0.391277
mean_h                      0.512652
mean_s                      0.561194
mean_v                      0.447482
dominant_r                  0.091864
dominant_g                  0.087105
dominant_b                  0.188235
dominant_h                   0.67451
dominant_s                  0.537255
dominant_v                  0.188235
black                       0.441732
gray                         0.03125
white                            0.0
orange                           0.0
orange-yellow               0.113932
yellow                      0.004774
yellow-green                     0.0
green                            0.0
green-blue                       0.0
blue                             0

index                     id   platform        hashtag n_clusters  \
4692      0     klimakrise_637.jpg  instagram     klimakrise          1   
3204      0  climatecrisis_348.jpg  instagram  climatecrisis          4   
963       0    6818577285403200774     tiktok  savetheplanet          8   
244       0    7088611506413210923     tiktok  climatechange          8   
3200      0  climatecrisis_344.jpg  instagram  climatecrisis          9   
728       0    7031904457256389934     tiktok  climatecrisis          6   
974       0    7216003623514410245     tiktok  savetheplanet          4   
3838      0  savetheplanet_386.jpg  instagram  savetheplanet         18   
1163      0    7121966214003330310     tiktok  savetheplanet          8   
2857      0  climatechange_667.jpg  instagram  climatechange          9   
867       0    7123487997189836037     tiktok  climatecrisis          8   
4252      0     klimakrise_189.jpg  instagram     klimakrise         12   
2464      0  climatechange_167.jpg  instagram  climatechange          3   
2833      0  climatechange_638.jpg  instagram  climatechange          8   
4644      0     klimakrise_589.jpg  instagram     klimakrise         14   
3231      0  climatecrisis_380.jpg  instagram  climatecrisis         10   
1980      0    7251949202383670555     tiktok    klimaschutz         10   
3799      0  savetheplanet_336.jpg  instagram  savetheplanet          8   
5308      0    klimaschutz_565.jpg  instagram    klimaschutz          9   
2290      0    7158499766060600582     tiktok    klimaschutz          4   
3150      0  climatecrisis_290.jpg  instagram  climatecrisis         18   
4726      0     klimakrise_672.jpg  instagram     klimakrise          9   
1035      0    6943656486740462854     tiktok  savetheplanet          6   
4894      0    klimaschutz_144.jpg  instagram    klimaschutz          6   
1515      0    7268755257319034145     tiktok     klimakrise          8   
1787      0    6991435332126346501     tiktok     klimakrise          7   
3855      0  savetheplanet_408.jpg  instagram  savetheplanet          8   
56        0    7208613662649568517     tiktok  climatechange          4   
878       0    7126885772573150507     tiktok  climatecrisis         13   
471       0    7162622353631972614     tiktok  climatechange         13   
3392      0  climatecrisis_547.jpg  instagram  climatecrisis         11   
3219      0  climatecrisis_366.jpg  instagram  climatecrisis         12   
4872      0    klimaschutz_122.jpg  instagram    klimaschutz          9   
1888      0    7187762658840448262     tiktok    klimaschutz         14   
1342      0    6913933767472090370     tiktok     klimakrise          6   
3707      0  savetheplanet_212.jpg  instagram  savetheplanet          8   
198       0    7272725341884402949     tiktok  climatechange         15   
1426      0    7215972728891788549     tiktok     klimakrise         14   
2886      0    climatecrisis_1.jpg  instagram  climatecrisis          3   
3619      0  savetheplanet_101.jpg  instagram  savetheplanet         12   
2643      0  climatechange_402.jpg  instagram  climatechange         10   
4150      0      klimakrise_84.jpg  instagram     klimakrise         10   
1782      0    7124335149638028550     tiktok     klimakrise         15   
4477      0     klimakrise_417.jpg  instagram     klimakrise          8   
3074      0  climatecrisis_210.jpg  instagram  climatecrisis          9   
4861      0    klimaschutz_110.jpg  instagram    klimaschutz         11   
2210      0    7151445718971059461     tiktok    klimaschutz         14   
4801      0     klimaschutz_49.jpg  instagram    klimaschutz          9   
1266      0    7286078499767504160     tiktok     klimakrise         18   
512       0    7249751281365994795     tiktok  climatecrisis          9   

        mean_r    mean_g    mean_b    mean_h    mean_s  ...  yellow-green  \
4692  0.984314  0.951344  0.899393  0.101961  0.086275  ...      0.000000   
3204  0.912204  0.870760  

In [ ]:
df_images["hashtag"].unique()

In [16]:
fp_output = "Data\\unified_color_data_birch.csv"
df_images.to_csv(fp_output)

In [17]:
df_simplified = df_images[["id", "mean_h", "mean_s", "mean_v", "dominant_h", "dominant_s", "dominant_v", "max_colorname"]]
df_simplified.head(30)

id    mean_h    mean_s    mean_v  dominant_h  dominant_s  \
0   7172368921318657322  0.512652  0.561194  0.447482    0.674510    0.537255   
1   7256810993311812907  0.379549  0.245650  0.607623    0.031373    0.400000   
2   7224978138751618305  0.451293  0.375548  0.275581    0.572549    0.254902   
3   7291671021827116334  0.464454  0.522460  0.420612    0.694118    0.462745   
4   7252904683222895918  0.319209  0.269828  0.562161    0.164706    0.286275   
5   7090944613141269802  0.336764  0.363224  0.582594    0.082353    0.200000   
6   7128671667647286533  0.086743  0.098203  0.027898    0.000000    0.000000   
7   7226171450653248810  0.513383  0.195625  0.410196    0.690196    0.176471   
8   7296494527450205471  0.459281  0.439545  0.443727    0.666667    1.000000   
9   7133813521732668674  0.757846  0.437839  0.596971    0.976471    0.286275   
10  7261305666403355930  0.470201  0.091729  0.418102    0.611765    0.121569   
11  7275482700780293418  0.591360  0.338524  0.427488    0.000000    0.000000   
12  7290893643920018721  0.032987  0.010577  0.997408    0.000000    0.000000   
13  7314087623910313259  0.243730  0.214858  0.612534    0.000000    0.000000   
14  7123291862604975366  0.640328  0.584699  0.297124    0.866667    1.000000   
15  7258669309034057002  0.327277  0.690222  1.178485    0.129412    0.301961   
16  7188063677331852549  0.247400  0.194425  0.240094    0.000000    0.000000   
17  7263149337570561323  0.325700  0.141840  0.681967    0.078431    0.125490   
18  7114367586757905669  0.357420  0.518272  0.409158    0.541176    0.894118   
19  7178885507227651330  0.461069  0.615948  0.533282    0.517647    0.705882   
20  7127279410591567150  0.600124  0.137435  0.515610    0.733333    0.090196   
21  7260887322357402885  0.505453  0.504250  0.524725    0.545098    0.592157   
22  7314050125091851551  0.580570  0.204236  0.635184    0.756863    0.109804   
23  7281640195907292448  0.229914  0.430287  0.616592    0.219608    0.411765   
24  7111807885230853382  0.219914  0.300855  0.204642    0.000000    0.000000   
25  7244516578585218331  0.855849  0.404216  0.899533    0.737255    0.121569   
26  7286673402717424903  0.390730  0.092693  0.482531    0.164706    0.058824   
27  6761421822320708870  0.554694  0.111746  0.618891    0.607843    0.115686   
28  7156301698414284037  0.585902  0.529979  1.006570    0.000000    0.000000   
29  7140723856125283590  0.536035  0.502496  0.514524    0.584314    0.709804   

    dominant_v  max_colorname  
0     0.188235          black  
1     0.858824           gray  
2     0.372549          black  
3     0.152941          black  
4     0.819608           gray  
5     0.782353  orange-yellow  
6     0.000000          black  
7     0.211765           gray  
8     0.007843           gray  
9     0.788235         orange  
10    0.325490           gray  
11    0.000000          black  
12    1.000000          white  
13    0.996078           gray  
14    0.019608          black  
15    0.501961  orange-yellow  
16    0.003922          black  
17    0.788235  orange-yellow  
18    0.521569    blue-violet  
19    0.443137           blue  
20    0.341176           gray  
21    0.596078    blue-violet  
22    0.890196     violet-red  
23    0.686275   yellow-green  
24    0.000000          black  
25    0.219608           gray  
26    0.474510           gray  
27    0.556863           gray  
28    0.192157           gray  
29    0.701961         violet

In [18]:
output_simplified_fp = "Data\\simple_color_birch.csv"
df_simplified.to_csv(output_simplified_fp)